# Scalar UDF Inlining
User-Defined Functions that are implemented in Transact-SQL and return a single data value are referred to as T-SQL Scalar User-Defined Functions. T-SQL UDFs are an elegant way to achieve code reuse and modularity across SQL queries. Some computations (such as complex business rules) are easier to express in imperative UDF form. UDFs help in building up complex logic without requiring expertise in writing complex SQL queries. Scalar UDF inlining, a feature under the **Intelligent Query Processing** suite of features. This feature improves the performance of queries that invoke scalar UDFs in SQL Server (starting with **SQL Server 2019**) and **Azure SQL Database**.

*This example will show you how upgrading to **Database Compatibility Level = 150** could improve performance of queries which leverage scalar UDFs.*

More information about this feature is available [here](https://docs.microsoft.com/en-us/sql/relational-databases/user-defined-functions/scalar-udf-inlining?view=sqlallproducts-allversions).

**Step 1**: Create an instance of SQL Server 2019 using a Docker image and restore the AdventureWorks database backup

You will need the **AdventureWorks2017** database for this exercise. If you don't have this sample database, then you download the sample database [here](https://github.com/Microsoft/sql-server-samples/releases/download/adventureworks/AdventureWorks2017.bak "AdventureWorks download")

Restore the copied AdventureWorks database backup into the container and restore the backup.

##### Docker Commands
>docker pull mcr.microsoft.com/mssql/server:2019-latest

>docker run -e "ACCEPT_EULA=Y" -e "SA_PASSWORD=`<A Strong Password`>" -p 1445:1433 --name sql2019demo -d mcr.microsoft.com/mssql/server:2019-latest

>docker cp ".\Downloads\AdventureWorks2017.bak" sql2019demo:/var/opt/mssql/data


In [1]:
-- Restore the AdventureWorks2017.bak file 
declare @datafilepath varchar(8000) = CAST(SERVERPROPERTY('InstanceDefaultDataPath') as varchar(4000)) + 'AdventureWorks2017.mdf'
declare @logfilepath varchar(8000) = CAST(SERVERPROPERTY('InstanceDefaultLogPath') as varchar(4000)) + 'AdventureWorks2017.ldf'
-- Replace the path with the appropriate file
declare @backupfile varchar(8000) = 'AdventureWorks2017.bak'
restore database AdventureWorks2017
from disk = @backupfile
with move 'AdventureWorks2017' to @datafilepath,
move 'AdventureWorks2017_log' to @logfilepath,
stats = 10, REPLACE

**Step 2:** See scalar UDF performance issues using an example
The below query calls scalar UDFs to get the the list price and remaining stock of the products in the invetory. You will notice that it returns over 121,000 rows.


In [12]:
USE AdventureWorks2017
GO
-- Set compatibility level to 140 to demonstrate performance impact with scalar UDFs
ALTER DATABASE AdventureWorks2017 SET compatibility_level = 140
GO
-- Execute the query
SELECT  OH.PurchaseOrderNumber , 
        dbo.ufnGetProductListPrice(OD.ProductID, OH.OrderDate) ListPrice ,
        OD.UnitPRice ,
        OD.OrderQty ,
        OD.LineTotal ,
        dbo.ufnGetStock(OD.ProductID) RemainingStock
FROM    Sales.SalesOrderHeader OH
        INNER JOIN Sales.SalesOrderDetail OD 
        ON OH.SalesOrderID = OD.SalesOrderID
OPTION (RECOMPILE)

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Displaying Top 5000 rows.

Total execution time: 00:00:06.286

PurchaseOrderNumber ListPrice UnitPRice OrderQty LineTotal RemainingStock PO522145787 3374.9900 2024.9940 1 2024.994000 0 PO522145787 3374.9900 2024.9940 3 6074.982000 0 PO522145787 3374.9900 2024.9940 1 2024.994000 0 PO522145787 3399.9900 2039.9940 1 2039.994000 0 PO522145787 3399.9900 2039.9940 1 2039.994000 0 PO522145787 3399.9900 2039.9940 2 4079.988000 0 PO522145787 3399.9900 2039.9940 1 2039.994000 0 PO522145787 48.0673 28.8404 3 86.521200 0 PO522145787 48.0673 28.8404 1 28.840400 0 PO522145787 9.5000 5.7000 6 34.200000 0 PO522145787 8.6442 5.1865 2 10.373000 0 PO522145787 33.6442 20.1865 4 80.746000 0 PO18850127500 699.0982 419.4589 1 419.458900 0 PO18850127500 1457.9900 874.7940 1 874.794000 0 PO18473189620 1349.6000 809.7600 1 809.760000 0 PO18473189620 1191.1739 714.7043 1 714.704300 0 PO18473189620 1191.1739 714.7043 2 1429.408600 0 PO18473189620 8.6442 5.1865 4 20.746000 0 PO18473189620 48.0673 28.8404 4 115.361600 0 PO18473189620 1204.3248 722.5949 2 1445.189800 0 PO18473189620 3374.9900 2024.9940 3 6074.982000 0 PO18473189620 3374.9900 2024.9940 2 4049.988000 0 PO18473189620 33.6442 20.1865 2 40.373000 0 PO18473189620 1364.5000 818.7000 2 1637.400000 0 PO18473189620 3374.9900 2024.9940 4 8099.976000 0 PO18473189620 3399.9900 2039.9940 2 4079.988000 0 PO18473189620 48.0673 28.8404 2 57.680800 0 PO18473189620 3374.9900 2024.9940 2 4049.988000 0 PO18473189620 33.6442 20.1865 5 100.932500 0 PO18444174044 699.0982 419.4589 3 1258.376700 0 PO18444174044 699.0982 419.4589 5 2097.294500 0 PO18444174044 306.5636 183.9382 2 367.876400 0 PO18444174044 1457.9900 874.7940 4 3499.176000 0 PO18444174044 306.5636 183.9382 3 551.814600 0 PO18444174044 699.0982 419.4589 5 2097.294500 0 PO18444174044 699.0982 419.4589 3 1258.376700 0 PO18444174044 699.0982 419.4589 2 838.917800 0 PO18444174044 3578.2700 2146.9620 1 2146.962000 0 PO18444174044 1457.9900 874.7940 1 874.794000 0 PO18444174044 699.0982 419.4589 3 1258.376700 0 PO18444174044 594.8300 356.8980 1 356.898000 0 PO18444174044 1457.9900 874.7940 6 5248.764000 0 PO18444174044 306.5636 183.9382 1 183.938200 0 PO18444174044 297.6346 178.5808 3 535.742400 0 PO18444174044 3578.2700 2146.9620 1 2146.962000 0 PO18444174044 699.0982 419.4589 3 1258.376700 0 PO18444174044 306.5636 183.9382 1 183.938200 0 PO18444174044 594.8300 356.8980 1 356.898000 0 PO18444174044 297.6346 178.5808 1 178.580800 0 PO18444174044 699.0982 419.4589 3 1258.376700 0 PO18444174044 1457.9900 874.7940 1 874.794000 0 PO18009186470 699.0982 419.4589 1 419.458900 0 PO16617121983 3399.9900 2039.9940 1 2039.994000 0 PO16617121983 3374.9900 2024.9940 4 8099.976000 0 PO16617121983 48.0673 28.8404 1 28.840400 0 PO16617121983 48.0673 28.8404 1 28.840400 0 PO16617121983 3374.9900 2024.9940 2 4049.988000 0 PO16617121983 3399.9900 2039.9940 3 6119.982000 0 PO16617121983 3399.9900 2039.9940 1 2039.994000 0 PO16617121983 3374.9900 2024.9940 1 2024.994000 0 PO16588191572 33.6442 20.1865 2 40.373000 0 PO16588191572 3399.9900 2039.9940 1 2039.994000 0 PO16588191572 33.6442 20.1865 1 20.186500 0 PO16588191572 48.0673 28.8404 2 57.680800 0 PO16588191572 3374.9900 2024.9940 2 4049.988000 0 PO16588191572 8.6442 5.1865 2 10.373000 0 PO16588191572 3374.9900 2024.9940 2 4049.988000 0 PO16588191572 3374.9900 2024.9940 1 2024.994000 0 PO16588191572 9.5000 5.7000 6 34.200000 0 PO16588191572 3374.9900 2024.9940 1 2024.994000 0 PO16008173883 699.0982 419.4589 1 419.458900 0 PO16008173883 3578.2700 2146.9620 1 2146.962000 0 PO16008173883 594.8300 356.8980 1 356.898000 0 PO16008173883 1457.9900 874.7940 1 874.794000 0 PO16008173883 699.0982 419.4589 2 838.917800 0 PO16008173883 699.0982 419.4589 1 419.458900 0 PO15428132599 9.5000 5.7000 3 17.100000 0 PO15428132599 3399.9900 2039.9940 1 2039.994000 0 PO15428132599 3374.9900 2024.9940 1 2024.994000 0 PO15428132599 3374.9900 2024.9940 1 2024.994000 0 PO14732180295 1457.9900 874.7940 3 2624.382000 0 PO14732180295 3578.2700 2146.9620 2 4293.924000 0 PO14732180295 699.0982 419.4589 7 2936.212300

**Step 3**: Let's use our query execution DMVs to determine how many times each of the scalar UDFs were executed. You will find that the UDFs were executed once for each row returned by the query. 

In [13]:
SET NOCOUNT ON;
SELECT  OBJECT_NAME (T.objectid) as [Function Name], QS.execution_count as [Execution Count]
FROM    sys.dm_exec_query_stats QS
        CROSS APPLY sys.dm_exec_sql_text(sql_handle) T
WHERE  T.objectid in (object_id('ufnGetStock'),object_id('ufnGetProductListPrice'));

-- Create an Extended Event session to track the UDF inlining 
CREATE EVENT SESSION [XE_InlineScalarUDF] ON SERVER 
ADD EVENT sqlserver.query_tsql_scalar_udf_inlined(
    ACTION(sqlserver.client_app_name,sqlserver.client_hostname,sqlserver.database_id,sqlserver.query_hash,sqlserver.query_plan_hash,sqlserver.session_id,sqlserver.sql_text,sqlserver.username)),
ADD EVENT sqlserver.tsql_scalar_udf_not_inlineable(
    ACTION(sqlserver.client_app_name,sqlserver.client_hostname,sqlserver.database_id,sqlserver.query_hash,sqlserver.query_plan_hash,sqlserver.session_id,sqlserver.sql_text,sqlserver.username))
ADD TARGET package0.event_file(SET filename=N'XE_InlineScalarUDF')
WITH (MAX_MEMORY=4096 KB,EVENT_RETENTION_MODE=ALLOW_SINGLE_EVENT_LOSS,MAX_DISPATCH_LATENCY=30 SECONDS,MAX_EVENT_SIZE=0 KB,MEMORY_PARTITION_MODE=NONE,TRACK_CAUSALITY=OFF,STARTUP_STATE=OFF)
GO


Commands completed successfully.

Total execution time: 00:00:00.030

Function Name Execution Count ufnGetProductListPrice 121317 ufnGetStock 121317

**Step 4**: Let us now look at how the perofrmance of the same query with inline UDFs. You will notice that his query finishes faster than what we saw in Step 3.

In [14]:
USE AdventureWorks2017
GO
-- Set compatibility level to 150 to demonstrate UDF inlining
ALTER DATABASE AdventureWorks2017 SET compatibility_level = 150
-- Start the Extended Event Session
ALTER EVENT SESSION [XE_InlineScalarUDF] ON SERVER STATE = START
ALTER DATABASE SCOPED CONFIGURATION CLEAR PROCEDURE_CACHE;
GO
-- Execute the query
SELECT  OH.PurchaseOrderNumber , 
        dbo.ufnGetProductListPrice(OD.ProductID, OH.OrderDate) ListPrice ,
        OD.UnitPRice ,
        OD.OrderQty ,
        OD.LineTotal ,
        dbo.ufnGetStock(OD.ProductID) RemainingStock
FROM    Sales.SalesOrderHeader OH
        INNER JOIN Sales.SalesOrderDetail OD 
        ON OH.SalesOrderID = OD.SalesOrderID
OPTION (RECOMPILE)
GO
-- Start the Extended Event Session
ALTER EVENT SESSION [XE_InlineScalarUDF] ON SERVER STATE = STOP


Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Displaying Top 5000 rows.

Commands completed successfully.

Total execution time: 00:00:01.608

PurchaseOrderNumber ListPrice UnitPRice OrderQty LineTotal RemainingStock PO13978119376 48.0673 28.8404 1 28.840400 0 PO12499138177 48.0673 28.8404 1 28.840400 0 PO2900174093 48.0673 28.8404 5 144.202000 0 PO8874137222 48.0673 28.8404 1 28.840400 0 PO3915123127 48.0673 28.8404 3 86.521200 0 PO8468183786 48.0673 28.8404 4 115.361600 0 PO16472151816 48.0673 28.8404 4 115.361600 0 PO3915144057 48.0673 28.8404 3 86.521200 0 PO11600132440 48.0673 28.8404 5 144.202000 0 PO16327170541 48.0673 28.8404 5 144.202000 0 PO14471123403 48.0673 28.8404 1 28.840400 0 PO10440182311 48.0673 28.8404 6 173.042400 0 PO1827149671 48.0673 28.8404 1 28.840400 0 PO1798140269 48.0673 28.8404 4 115.361600 0 PO1189177803 48.0673 28.8404 2 57.680800 0 PO5191115657 48.0673 28.8404 2 57.680800 0 PO6438197212 48.0673 28.8404 2 57.680800 0 PO10701186775 48.0673 27.8790 13 355.178460 0 PO6786128920 48.0673 27.8790 12 327.857040 0 PO3538157862 48.0673 28.8404 2 57.680800 0 PO4495116659 48.0673 28.8404 3 86.521200 0 PO6235159004 48.0673 28.8404 1 28.840400 0 PO8787194061 48.0673 28.8404 8 230.723200 0 PO14993121765 48.0673 28.8404 1 28.840400 0 PO6641155631 48.0673 28.8404 3 86.521200 0 PO16617121983 48.0673 28.8404 1 28.840400 0 PO16733124458 48.0673 28.8404 1 28.840400 0 PO2030112412 48.0673 28.8404 2 57.680800 0 PO4901196283 48.0673 28.8404 2 57.680800 0 PO12586158748 48.0673 28.8404 1 28.840400 0 PO10817110834 48.0673 28.8404 4 115.361600 0 PO9831178966 48.0673 27.8790 12 327.857040 0 PO522145787 48.0673 28.8404 1 28.840400 0 PO10817150168 48.0673 28.8404 1 28.840400 0 PO7859187017 48.0673 28.8404 4 115.361600 0 PO11919119101 48.0673 28.8404 1 28.840400 0 PO1827151513 48.0673 28.8404 1 28.840400 0 PO8845169807 48.0673 28.8404 2 57.680800 0 PO17545123793 48.0673 27.8790 11 300.535620 0 PO5597154214 48.0673 28.8404 8 230.723200 0 PO9570119946 48.0673 28.8404 1 28.840400 0 PO7859142972 48.0673 28.8404 10 288.404000 0 PO14732180295 48.0673 28.8404 1 28.840400 0 PO5858178400 48.0673 28.8404 1 28.840400 0 PO4901118407 48.0673 28.8404 4 115.361600 0 PO18299142683 48.0673 28.8404 3 86.521200 0 PO17574111786 48.0673 28.8404 6 173.042400 0 PO9483189305 48.0673 28.8404 5 144.202000 0 PO19343197973 48.0673 28.8404 9 259.563600 0 PO18299110324 48.0673 28.8404 5 144.202000 0 PO18473189620 48.0673 28.8404 2 57.680800 0 PO8120182325 48.0673 28.8404 3 86.521200 0 PO9657130250 48.0673 28.8404 3 86.521200 0 PO16327172067 48.0673 28.8404 6 173.042400 0 PO12586178184 48.0673 28.8404 3 86.521200 0 PO11484122930 48.0673 28.8404 5 144.202000 0 PO3509195138 48.0673 28.8404 7 201.882800 0 PO6699130779 48.0673 28.8404 4 115.361600 0 PO5858128971 48.0673 28.8404 4 115.361600 0 PO261128364 48.0673 28.8404 2 57.680800 0 PO7656175368 48.0673 28.8404 3 86.521200 0 PO19488118734 48.0673 28.8404 2 57.680800 0 PO15138128112 48.0673 28.8404 4 115.361600 0 PO10614138214 48.0673 28.8404 3 86.521200 0 PO2813155355 48.0673 28.8404 7 201.882800 0 PO12644161356 48.0673 28.8404 10 288.404000 0 PO2494191557 48.0673 28.8404 8 230.723200 0 PO6467187386 48.0673 28.8404 5 144.202000 0 PO12499190711 48.0673 28.8404 3 86.521200 0 PO10440184078 48.0673 28.8404 5 144.202000 0 PO12557127067 48.0673 28.8404 4 115.361600 0 PO11600128380 48.0673 28.8404 1 28.840400 0 PO3799116239 48.0673 28.8404 2 57.680800 0 PO11861165059 9.5000 5.7000 4 22.800000 0 PO8120182325 9.5000 5.7000 6 34.200000 0 PO19923118772 9.5000 5.7000 2 11.400000 0 PO12586178184 9.5000 5.7000 2 11.400000 0 PO2146148184 9.5000 5.7000 3 17.100000 0 PO5858128971 9.5000 5.7000 1 5.700000 0 PO5800111159 9.5000 5.7000 2 11.400000 0 PO17574182721 9.5000 5.7000 4 22.800000 0 PO16211194171 9.5000 5.7000 4 22.800000 0 PO14529112624 9.5000 5.7000 2 11.400000 0 PO2726163521 9.5000 5.7000 4 22.800000 0 PO12586158748 9.5000 5.7000 6 34.200000 0 PO5568111446 9.5000 5.7000 2 11.400000 0 PO6438146078 9.5000 5.7000 4 22.800000 0 PO7221197705 9.5000 5.7000 3 17.100000 0 PO16037118184 9.5000 5.7000 2 11.400000 0 PO10759149389 9.5000 5.7000 10 57.000000 0 PO144711234

**Step 5**: Use the extended event session to find out if the UDF got inlined.

In [15]:
-- Look at how many UDF calls got inlined
DECLARE @filename varchar(8000) ;
SELECT @filename = CAST(target_data as XML).value('(/EventFileTarget/File/@name)[1]', 'varchar(8000)')
FROM sys.dm_xe_session_targets
WHERE target_name = 'event_file' and event_session_address = (select address from sys.dm_xe_sessions where name = 'system_health');

SET @filename = SUBSTRING(@filename,1,CHARINDEX('system_health',@filename,1)-1) + '*.xel';

-- Read the XEL files to get the System Health Session Data
SELECT object_name as [XE Name],CAST(event_data as XML) as [XE Data]
FROM sys.fn_xe_file_target_read_file(@filename, null, null, null)
WHERE object_name = 'query_tsql_scalar_udf_inlined'



**Step 6**: Find out all the different functions in the database that can be inlined

In [7]:
USE AdventureWorks2017
GO
select object_name(object_id), definition from sys.sql_modules where is_inlineable = 1

Commands completed successfully.

(10 rows affected)

Total execution time: 00:00:00.022

(No column name) definition ufnGetAccountingStartDate 
CREATE FUNCTION [dbo].[ufnGetAccountingStartDate]()
RETURNS [datetime] 
AS 
BEGIN
 RETURN CONVERT(datetime, '20030701', 112);
END;
 ufnGetAccountingEndDate 
CREATE FUNCTION [dbo].[ufnGetAccountingEndDate]()
RETURNS [datetime] 
AS 
BEGIN
 RETURN DATEADD(millisecond, -2, CONVERT(datetime, '20040701', 112));
END;
 ufnGetProductDealerPrice 


CREATE FUNCTION [dbo].[ufnGetProductDealerPrice](@ProductID [int], @OrderDate [datetime])
RETURNS [money] 
AS 
-- Returns the dealer price for the product on a specific date.
BEGIN
 DECLARE @DealerPrice money;
 DECLARE @DealerDiscount money;

 SET @DealerDiscount = 0.60 -- 60% of list price

 SELECT @DealerPrice = plph.[ListPrice] * @DealerDiscount 
 FROM [Production].[Product] p 
 INNER JOIN [Production].[ProductListPriceHistory] plph 
 ON p.[ProductID] = plph.[ProductID] 
 AND p.[ProductID] = @ProductID 
 AND @OrderDate BETWEEN plph.[StartDate] AND COALESCE(plph.[EndDate], CONVERT(datetime, '99991231', 112)); -- Make sure we get all the prices!

 RETURN @DealerPrice;
END;
 ufnGetProductListPrice 
CREATE FUNCTION [dbo].[ufnGetProductListPrice](@ProductID [int], @OrderDate [datetime])
RETURNS [money] 
AS 
BEGIN
 DECLARE @ListPrice money;

 SELECT @ListPrice = plph.[ListPrice] 
 FROM [Production].[Product] p 
 INNER JOIN [Production].[ProductListPriceHistory] plph 
 ON p.[ProductID] = plph.[ProductID] 
 AND p.[ProductID] = @ProductID 
 AND @OrderDate BETWEEN plph.[StartDate] AND COALESCE(plph.[EndDate], CONVERT(datetime, '99991231', 112)); -- Make sure we get all the prices!

 RETURN @ListPrice;
END;
 ufnGetProductStandardCost 
CREATE FUNCTION [dbo].[ufnGetProductStandardCost](@ProductID [int], @OrderDate [datetime])
RETURNS [money] 
AS 
-- Returns the standard cost for the product on a specific date.
BEGIN
 DECLARE @StandardCost money;

 SELECT @StandardCost = pch.[StandardCost] 
 FROM [Production].[Product] p 
 INNER JOIN [Production].[ProductCostHistory] pch 
 ON p.[ProductID] = pch.[ProductID] 
 AND p.[ProductID] = @ProductID 
 AND @OrderDate BETWEEN pch.[StartDate] AND COALESCE(pch.[EndDate], CONVERT(datetime, '99991231', 112)); -- Make sure we get all the prices!

 RETURN @StandardCost;
END;
 ufnGetStock 
CREATE FUNCTION [dbo].[ufnGetStock](@ProductID [int])
RETURNS [int] 
AS 
-- Returns the stock level for the product. This function is used internally only
BEGIN
 DECLARE @ret int;
 
 SELECT @ret = SUM(p.[Quantity]) 
 FROM [Production].[ProductInventory] p 
 WHERE p.[ProductID] = @ProductID 
 AND p.[LocationID] = '6'; -- Only look at inventory in the misc storage
 
 IF (@ret IS NULL) 
 SET @ret = 0
 
 RETURN @ret
END;
 ufnGetDocumentStatusText 
CREATE FUNCTION [dbo].[ufnGetDocumentStatusText](@Status [tinyint])
RETURNS [nvarchar](16) 
AS 
-- Returns the sales order status text representation for the status value.
BEGIN
 DECLARE @ret [nvarchar](16);

 SET @ret = 
 CASE @Status
 WHEN 1 THEN N'Pending approval'
 WHEN 2 THEN N'Approved'
 WHEN 3 THEN N'Obsolete'
 ELSE N'** Invalid **'
 END;
 
 RETURN @ret
END;
 ufnGetPurchaseOrderStatusText 
CREATE FUNCTION [dbo].[ufnGetPurchaseOrderStatusText](@Status [tinyint])
RETURNS [nvarchar](15) 
AS 
-- Returns the sales order status text representation for the status value.
BEGIN
 DECLARE @ret [nvarchar](15);

 SET @ret = 
 CASE @Status
 WHEN 1 THEN 'Pending'
 WHEN 2 THEN 'Approved'
 WHEN 3 THEN 'Rejected'
 WHEN 4 THEN 'Complete'
 ELSE '** Invalid **'
 END;
 
 RETURN @ret
END;
 ufnGetSalesOrderStatusText 
CREATE FUNCTION [dbo].[ufnGetSalesOrderStatusText](@Status [tinyint])
RETURNS [nvarchar](15) 
AS 
-- Returns the sales order status text representation for the status value.
BEGIN
 DECLARE @ret [nvarchar](15);

 SET @ret = 
 CASE @Status
 WHEN 1 THEN 'In process'
 WHEN 2 THEN 'Approved'
 WHEN 3 THEN 'Backordered'
 WHEN 4 THEN 'Rejected'
 WHEN 5 THEN 'Shipped'
